Getting the name of all nodes in Neo4j

In [2]:
from neo4j import GraphDatabase, basic_auth
uri = 'bolt://localhost:7687'

driver = GraphDatabase.driver(uri, auth=("neo4j", "password"))

Getting all nodes

In [3]:
cypher_query = '''
MATCH (n) RETURN (n);
'''

In [4]:
with driver.session(database="neo4j") as session:
  results = session.read_transaction(
    lambda tx: tx.run(cypher_query).data())

driver.close()

/var/folders/02/s19kvgxj5l7d6sjlnmcpqd8c0000gn/T/ipykernel_7966/1473302897.py:2: DeprecationWarning: read_transaction has been renamed to execute_read
  results = session.read_transaction(


In [5]:
results[0]

# for node in results:
#     print(node)

{'n': {'sourceID': 'Panama Papers',
  'address': 'ORION HOUSE SERVICES (HK) LIMITED ROOM 1401; 14/F.; WORLD COMMERCE  CENTRE; HARBOUR CITY; 7-11 CANTON ROAD; TSIM SHA TSUI; KOWLOON; HONG KONG',
  'internal_id': '1001256',
  'jurisdiction': 'SAM',
  'struck_off_date': '15-FEB-2013',
  'service_provider': 'Mossack Fonseca',
  'countries': 'Hong Kong',
  'jurisdiction_description': 'Samoa',
  'lastEditTimestamp': '1638311020926',
  'valid_until': 'The Panama Papers data is current through 2015',
  'ibcRUC': '25221',
  'original_name': 'TIANSHENG INDUSTRY AND TRADING CO., LTD.',
  'name': 'TIANSHENG INDUSTRY AND TRADING CO., LTD.',
  'country_codes': 'HKG',
  'inactivation_date': '18-FEB-2013',
  'incorporation_date': '23-MAR-2006',
  'status': 'Defaulted',
  'node_id': 10000001}}

Reading in the PEP dataset

In [6]:
import pandas as pd
import numpy as np

In [7]:
df_pep = pd.read_csv('../cse_6242_project/02.data/targets.simple.csv')

In [8]:
df_pep.head()

id  schema                  name aliases birth_date countries  \
0  eu-cor-2011996  Person  GAMALLO ALLER, Jesús     NaN        NaN        es   
1  eu-cor-2012064  Person     KUHN-THEIS, Helma     NaN        NaN        de   
2  eu-cor-2014776  Person    RICHSTEIN, Barbara     NaN        NaN        de   
3  eu-cor-2015290  Person      MÜÜRSEPP, Kurmet     NaN        NaN        ee   
4  eu-cor-2015349  Person       SMRDELJ, Robert     NaN        NaN        si   

                                     addresses identifiers  sanctions  \
0    Rúa do Hórrero 61, Santiago De Compostela         NaN        NaN   
1                   Zuckerberg 35, Weiskirchen         NaN        NaN   
2                       Alter Markt 1, Potsdam         NaN        NaN   
3  Kesk 12, Kobela, Kobela alevik, Antsla vald         NaN        NaN   
4                         Kolodvorska 5, Pivka         NaN        NaN   

           phones                                             emails  \
0    +34981541002                                  sunioneu@xunta.es   
1  +4915162403454                              h.kuhntheis@gmail.com   
2   +493319661010  barbara.richstein@landtag.brandenburg.de;kist-...   
3     +3725179213                               kurmetster@gmail.com   
4    +38657210100                     obcina@pivka.si;zupan@pivka.si   

                                           dataset           first_seen  \
0  Members of the European Commitee of the Regions  2021-07-26 11:55:45   
1  Members of the European Commitee of the Regions  2022-07-18 00:51:28   
2  Members of the European Commitee of the Regions  2021-07-26 11:55:45   
3  Members of the European Commitee of the Regions  2021-07-26 11:55:45   
4  Members of the European Commitee of the Regions  2021-07-26 11:55:45   

             last_seen  
0  2023-03-14 12:03:15  
1  2023-03-14 12:03:15  
2  2023-03-14 12:03:15  
3  2023-03-14 12:03:15  
4  2023-03-14 12:03:15

Attempting a fuzzy match

In [24]:
from fuzzywuzzy import process

In [10]:
pep_names = [name for name in df_pep['name']]

In [19]:
options = list(zip(df_pep['id'], df_pep['name']))

In [34]:
print(options)

[('eu-cor-2011996', 'GAMALLO ALLER, Jesús'), ('eu-cor-2012064', 'KUHN-THEIS, Helma'), ('eu-cor-2014776', 'RICHSTEIN, Barbara'), ('eu-cor-2015290', 'MÜÜRSEPP, Kurmet'), ('eu-cor-2015349', 'SMRDELJ, Robert'), ('eu-cor-2015355', 'ŽAGAR, Ivan'), ('eu-cor-2015368', 'IWANIUK, Krzysztof'), ('eu-cor-2015646', 'KOURAKIS, Ioannis'), ('eu-cor-2015768', 'CAVERI, Luciano Emilio'), ('eu-cor-2015885', 'MALINAUSKAS, Ričardas'), ('eu-cor-2016308', 'LECH, Mirosław'), ('eu-cor-2018538', 'AZZOPARDI, Samuel'), ('eu-cor-2018609', 'BIWER, Roby'), ('eu-cor-2019024', 'ALVES CORDEIRO, Vasco'), ('eu-cor-2019046', 'IVANOV, Emil'), ('eu-cor-2019725', 'DRĂGHICI, Emil'), ('eu-cor-2019896', 'MOSKOV, Vladimir'), ('eu-cor-2019897', 'ZHIVKOV, Zlatko'), ('eu-cor-2020166', 'ABRAMAVIČIUS, Arnoldas'), ('eu-cor-2020203', 'ŽAGUNIS, Povilas'), ('eu-cor-2020242', 'WOŹNIAK, Marek'), ('eu-cor-2020443', 'NICA, Alin-Adrian'), ('eu-cor-2020472', 'VĪTOLIŅŠ, Jānis'), ('eu-cor-2021132', 'GJESING, Jens Christian'), ('eu-cor-2021625', 'P

In [36]:
print(results[0])

In [35]:
vals = [process.extract(results[i]['n']['name'], [option[1] for option in options], limit=1) for i in results]

TypeError: list indices must be integers or slices, not dict